# Frequency tests for comments 
This notebook is the analysis for identifying common and rare words within and outside of r/science (Table 2). 
This includes for first time and recurrent commenters in r/science.

In [1]:
import re
import csv
import json
import string
from collections import Counter

import spacy
import numpy as np
import pandas as pd
from scipy import stats


import os 
os.chdir('/homes/gws/taugust/Projects/ARK/community_guidelines/')

all_posts_dir = 'data/cleaned/full_real_subs_cleaned_posts_2018_short.csv'
all_comments_dir = 'data/cleaned/full_real_subs_cleaned_comments_2018_short.csv'

In [2]:
# define a quick and simple tokenizer
# (FWIW: I'm pretty sure I created this for something else, it's not perfect but ...
# ... the point is to remove punctuation somewhat sensibly, lower case, and split)

punct_chars = list(set(string.punctuation) - set("'"))
punct_chars.sort()
punctuation = ''.join(punct_chars)
replace = re.compile('[%s]' % re.escape(punctuation))

def text_to_tokens(text, lower=True, ngram=None):
    # replace underscores with spaces
    text = re.sub(r'_', ' ', text)
    # break off single quotes at the ends of words (e.g. 'test' -> test)
    text = re.sub(r'\s\'', ' ', text)
    text = re.sub(r'\'\s', ' ', text)
    # remove periods (e.g. U.S. -> US)
    text = re.sub(r'\.', '', text)
    # replace all other punctuation (except single quotes) with spaces (e.g. T-rex -> t rex)
    text = replace.sub(' ', text)
    # remove single quotes (e.g. don't -> dont)
    text = re.sub(r'\'', '', text)
    # replace all whitespace with a single space
    text = re.sub(r'\s', ' ', text)
    # strip off spaces on either end
    text = text.strip()    
    if lower:
        text = text.lower()
    split_text = text.split()
    if ngram is None:
        return split_text
    else:
        return [tuple(split_text[i:i+ngram]) for i in range(len(split_text)-ngram+1)]
    
# convert list for bigrams to tuple
def convert_to_tuple(line, cols):
    for col in cols:
        line[col] = [tuple(bigram) for bigram in line[col]]
    return line
        

In [6]:

# # do the same thing for comments
# header = True
# comments = []
# print(all_comments_dir)
# # infile = '../../../zinhome/dallas/reddit/all_comments_2018.csv'
# i = 0
# with open(all_comments_dir, 'r') as csvfile:
#     spamreader = csv.reader(csvfile, delimiter=',', quotechar='"', escapechar='\\')
#     for row in spamreader:
#         if i % 10000 == 0:
#             print("{:d}".format(i), end="\r", flush=True)
#         if header:
#             header = False
#             print(row)
#         if i == 0:
#             print(row)
#         else:
#             body = row[1]
#             author = row[2] #changed from 2
# #             score = row[4] #changed from 4
#             subreddit = row[3] # changed from 5
#             month = row[4] #changed from 7
#             comments.append({'id': 'c' + str(i), 'subreddit': subreddit, 'author': str(author),  'body': str(body), 'month': int(month)})
#             i += 1

# print(len(comments))

# with open('all_comments_2018_unparsed.jsonlist', 'w') as f:
#     for line in comments:
#         f.write(json.dumps(line) + '\n')


data/cleaned/full_real_subs_cleaned_comments_2018_short.csv
['kind', 'body', 'author', 'subreddit', 'created_month']
['kind', 'body', 'author', 'subreddit', 'created_month']
['comment', "The rest of the world doesn't decide the US presidency, what they say doesn't matter", 'The_Doodly_Danger', 'news', '9']
['comment', '"They can sleep in the Mississippi mud under a bridge and out of view of any business and people will still come after them." - sorry but not really buying this', 'futmaster420', 'news', '9']
['comment', '&gt; Elon is an ass\n\nBut not allowing workers to unionize *is* an ass thing to do.', 'Felinomancy', 'news', '9']
['comment', "Was the boy carrying? If he didn't have a gun to protect himself it was kinda his own fault. Shame but he had it coming. ", 'SeverelyAshamed', 'news', '9']
['comment', 'Is it inappropriate to ask your coworkers for sexual favors, yes or no?', 'MrPookPook', 'news', '9']
['comment', "Good question. This isn't my area of expertise (I am a special 

['comment', "I see. He's a special events coordinator for Pulaski County Youth Services. He left the partisan position 20 months ago.\n\nYet this story author and editors needed to lead with Democratic Party in the headline, in a story the day of the election. Gee whiz, I wonder why.", 'copperplatedbowl', 'news', '11']
['comment', 'You can volunteer for 20 hrs a week and look for jobs in the meanwhile. You have more than enough time. I work 45hrs a week, go to school part time, and would still have enough time to find a job.', 'AlexThugNastyyy', 'news', '11']
['comment', "I had quick acess safe even when I lived by myself; I don't want to worry that friends or family potentially with young children may be stopping by for a visit unannounced and I have an unsecured firearm laying around somewhere. Seriously, $100 nightstand safe for your $500 handgun is a good investment.", 'Mccalltx', 'news', '11']
['comment', "Try making an associates work for you.  I can't remember the last time I he

['comment', 'taking cover behind a car facing off a guy against a guy hundreds of feet away armed with (maybe) a handgun is a very fucking safe place to be', 'beer_nyc', 'news', '6']
['comment', 'Yeah, probably. Not sure whether the fascists or communists (or neither)  would have won, though.', 'mrchaotica', 'news', '6']
['comment', 'You might want a teacher with slightly more average looks if you want sex ed to become a normal mainstream thing.', 'Astilaroth', 'news', '5']
['comment', '*illegal immigrants\n\nFTFY\n\nThey’re breaking the law. \n\nFunny how you forgot to mention that one minor detail. ICE has no issues with legal immigrants.', 'W0NdERSTrUM', 'news', '8']
['comment', 'You mean guys trying to manipulate women into fucking them, at best.  At worst, well...    \n\nYou know how most people connect and speak to women they are attracted to?  They just talk to them, like a fucking human being. ', 'pornoforpiraters', 'news', '9']
['comment', 'I teach and I’d much rather keep my 

['comment', 'Or, and bear with me because this is crazy, we could have more children ourselves instead of outsourcing that job to foreign nations. I know, it sounds nuts.', 'almond_activator', 'news', '8']
['comment', 'This happened Wednesday morning.  They just make the episodes that quickly. ', 'AdmonishTrousers', 'news', '12']
['comment', '"innocent passage" is relevant when you are in territorial waters of a country that might not like you. I was responding to the situation in international waters (i.e. when you\'re outside of such territorial waters).', 'aaaaaaaarrrrrgh', 'news', '3']
['comment', 'That guy didn’t follow every command, he reached for his pants. ', 'Hank-the-Pigeon', 'news', '6']
['comment', 'I have never seen or heard of a human defecate while standing.  The most advantageous method would actually be to squat.  Toilets are not the best configuration for such purposes, and even to this day, the evolutionary trend has triumphed.  (A better configuration would be to h

['comment', '"She said stop or no several times. She said that she doesn\'t want to, but she has made herself available. Afterwards I apologized. But she never screamed."\n\n', 'Foxbox405', 'news', '9']
['comment', "One I always use at Pizza Hut is TEOMED3T6 (enough to the point where I have it memorized). It's a three topping medium for $6. Unfortunately, they now charge a dollar extra for pan pizza, which is just patently offensive. Couldn't they just change the deal to a medium pizza for $7, since it would be criminal to get anything that isn't a pan pizza to begin with?", 'Justin__D', 'news', '8']
['comment', "There literally isn't even a post about this anywhere close to the front page, or even the fifth page, so what the hell are you guys talking?\n\nEven the threads which *do* exist are mostly sympathetic to him.", 'apricotasd28', 'news', '6']
['comment', "Maybe Florida needs to take a look at how it does things. You do know that people in New York 'joke' about moving to Florida

...

['comment', 'He wants to go to China and save on air miles.', 'smits017', 'news', '1']
['comment', "From your own source:\n\n&gt;An emergency situation is\xa0staged\xa0and researchers\xa0measure\xa0how long it takes the participants to intervene, if they intervene. These experiments have found that the presence of others inhibits helping, often by a large margin.For example, Bibb Latané and Judith Rodin (1969) staged an experiment around a woman in distress. 70 percent of the people alone called out or went to help the woman after they believed she had fallen and was hurt, but when there were other people in the room only 40 percent offered help.\n\nFeel free to post something I missed that says bystander effect does not exist.\n\nAnecdotally I can tell you it is extremely difficult to get anyone in a crowd to help, even something simple as calling 911. This is especially true when the emergency involves violence. I've seen it more times than I can count; everyone assumes someone else 

['comment', "So you're just going to ignore the specific examples already given in favor of just saying shit?\n\nYou're not proving your point, you're just proving your willingness to hold and defend an opinion regardless of your own ignorance.", 'ParanoydAndroid', 'news', '6']
['comment', 'I consider the article fake news created to stir up hate. The guy who ran the center was only looking out for them since he did not call for the bus. ', 'eworden', 'news', '10']
['comment', "You're right, and firearms accidents are incredibly unlikely, but both CCP holder crimes and firearms accidents are far, far more common than school shootings (and that's not to mention theft of the gun), which means that the net increased risk of adding guns to schools is greater than the potential for heroism. \n\nEdit: missed a word (crimes after CCP holder).", 'yoda133113', 'news', '5']
['comment', 'I said a racist would be *more* likely to sue. ', 'mboop127', 'news', '7']
['comment', 'Grunts gonna be eating

['comment', "Should local authorities let ICE know when they are releasing an illegal immigrant accused of a violent crime? You bet your ass, but that doesn't stop sanctuary cities.", 'NotArmchairAttorney', 'news', '12']
['comment', "that's the original question, not the completely different one he pointed out was not the same.", 'McFeely_Smackup', 'news', '2']
['comment', 'The media is fucking retarded. To them, every rifle is an assault rifle, every pistol is a Glock, and every armored vehicle is a tank.', 'Owl02', 'news', '2']
['comment', 'Humans are more important than animals. You must be the lesser you are talking about, decent humans don’t look at others like you seem to do. You’re not better than anyone with those standards. Get off your high horse, pal. ', 'jospa27', 'news', '2']
['comment', "When you offer a starving person money for sex, wouldn't you say that complicates the issue of consent just a bit?", 'wingedcoyote', 'news', '2']
['comment', 'Thanks for explaining it lik

['comment', "Y'all realize banning guns won't stop people from obtaining them correct?", 'gab_owns0', 'news', '11']
['comment', 'It\'s all garbage.  Stop watching cable news people!  They *need* 24 hours of "engaging" U.S. content every single day, but if there is nothing legitimately important happening they have no choice but to fill time with cheap, petty squabbles and manufactured controversy. These news corporations have no goals other than increasing market share and profits.', 'gurg2k1', 'news', '2']
['comment', 'wow, looking at your past posts, you are one small tiny bigot.\n\nWhat a pussy you are.  You hateful little child.', 'RememberSlimer', 'news', '2']
['comment', "It's gotten pretty ridiculous the last few years. It's to the point now that 90% of all calls to my cell phone are spam.", 'CreamOfSumYungFella', 'news', '6']
['comment', 'Yeah, I was going to say, the original looked pretty cartoonish too, except the colors had faded. This is nothing like the "ecce homo" (monke

['comment', 'Is there a society somewhere that doesn’t have famous people? I’d say this is pretty universal. So saying we should stop is a nice thought but...good luck with that.', 'Zazenp', 'news', '4']
['comment', '&gt; She never made any tribal claims at all.\n\nShe said she was Cherokee which is why the tribe put out a statement. Otherwise I doubt they would have commented.\n', 'FuriousChef', 'news', '10']
['comment', "ha ha ha ha. This is hilarious. Are you seriously saying slavery doesn't exist under communism and only exists under capitalism?\n\nNext you're going to tell me no one has ever tried true communism, right?", 'EldragonFromSA', 'news', '3']
['comment', 'It sounds nice to say " Victims need to be believed", but you\'re missing the implication there - you cannot logically and simultaneously believe in the truth of the accusation and the innocence of the accused.  I\'m not saying we should automatically assume that an accuser is lying; I\'m saying that we should neither b

In [ ]:
# with open('all_comments_2018_unparsed.jsonlist') as f:
#     comments = f.readlines()
# comments = [json.loads(line) for line in comments]     
# print(len(comments))

In [ ]:
# i = 1
# with open('all_comments_2018.jsonlist', 'w') as outfile:
#     with open('all_comments_2018_unparsed.jsonlist') as infile:
#         for line in infile:
#             if i % 10000 == 0:
#                 print("{:d}".format(i), end="\r", flush=True)            
#             comment = json.loads(line)
#             comment['body_tokens'] = text_to_tokens(comment['body'], ngram=1)
#             outfile.write(json.dumps(comment) + '\n')
#             i += 1
# print("")
# print("Done!")

In [ ]:
# i = 1
# with open('all_comments_2018.jsonlist', 'w') as outfile:
#     with open('all_comments_2018_unparsed.jsonlist') as infile:
#         for line in infile:
#             if i % 10000 == 0:
#                 print("{:d}".format(i), end="\r", flush=True)            
#             comment = json.loads(line)
#             comment['body_tokens'] = text_to_tokens(comment['body'], ngram=1)
#             outfile.write(json.dumps(comment) + '\n')
#             i += 1
# print("")
# print("Done!")

In [ ]:
# i = 1
# with open('all_comments_2018.jsonlist', 'w') as outfile:
#     with open('all_comments_2018_unparsed.jsonlist') as infile:
#         for line in infile:
#             if i % 10000 == 0:
#                 print("{:d}".format(i), end="\r", flush=True)            
#             comment = json.loads(line)
#             comment['body_tokens'] = text_to_tokens(comment['body'], ngram=1)
#             outfile.write(json.dumps(comment) + '\n')
#             i += 1
# print("")
# print("Done!")

In [ ]:
science_comment_counts = Counter()
bg_comment_counts = Counter()

with open('all_comments_2018.jsonlist') as f:
    for line_i, line in enumerate(f):
        if line_i % 10000 == 0:
            print("{:d}".format(line_i), end="\r", flush=True)                    
        line = json.loads(line)
        line = convert_to_tuple(line, ['body_tokens'])
        if line['subreddit'] == 'EverythingScience':
            science_comment_counts.update(line['body_tokens'])        
        else:
            bg_comment_counts.update(line['body_tokens'])        
print("")
print(len(science_comment_counts))
print(len(bg_comment_counts))

In [ ]:
print(len(science_comment_counts))
print(len(bg_comment_counts))
common = set()
common.update(science_comment_counts.keys())
common.update(bg_comment_counts.keys())
common = list(common)
common.sort()
print(len(common))
science_comments_N = sum(science_comment_counts.values())
bg_comments_N = sum(bg_comment_counts.values())
print(science_comments_N, bg_comments_N)

In [ ]:
smoothing = 0.1
vocab_size = len(common)
logprobs = []
pvals = []
for word in common:
    if word in bg_comment_counts:
        bg_c = bg_comment_counts[word] + smoothing
        bg_p = (bg_comment_counts[word] + smoothing) / float(bg_comments_N + smoothing * len(common))
    else:
        bg_c = smoothing
        bg_p = (smoothing) / float(bg_comments_N + smoothing * len(common))
    if word in science_comment_counts:
        count = science_comment_counts[word]
    else:
        count = 0
    logprob = stats.binom.logpmf(k=count, n=science_comments_N, p=bg_p)
    logprobs.append(logprob)
    chisq, pval = stats.chisquare([count, science_comments_N - count], 
                              [bg_c, bg_comments_N + smoothing * vocab_size - bg_c])
    pvals.append(pval * vocab_size)
print(len(logprobs))

In [ ]:
# order = np.argsort(logprobs)
# df = pd.DataFrame(columns=['word', 'logprob', 'pval', 'science_freq', 'bg_freq'])
# for i in range(50000):
#     word = common[order[i]]
#     if word in science_comment_counts:
#         sc_count = science_comment_counts[word]
#     else:
#         sc_count = 0
#     if word in bg_comment_counts:
#         bg_count = bg_comment_counts[word]
#     else:
#         bg_count = 0
#     if sc_count / science_comments_N > bg_count / bg_comments_N:
#         df.loc[i] = [word, logprobs[order[i]], pvals[order[i]], sc_count / science_comments_N, bg_count / bg_comments_N]
# df = df.sort_values(['logprob', 'science_freq'],  ascending=[True, False])        
# df.to_csv('common_in_askscience_comments.csv')
# print(df.head(n=50))

In [ ]:
# df = pd.DataFrame(columns=['word', 'logprob', 'pval', 'science_freq', 'bg_freq'])
# for i in range(50000):
#     word = common[order[i]]
#     if word in science_comment_counts:
#         sc_count = science_comment_counts[word]
#     else:
#         sc_count = 0
#     if word in bg_comment_counts:
#         bg_count = bg_comment_counts[word]
#     else:
#         bg_count = 0
#     if sc_count / science_comments_N < bg_count / bg_comments_N:
#         df.loc[i] = [word, logprobs[order[i]], pvals[order[i]], sc_count / science_comments_N, bg_count / bg_comments_N]
# df = df.sort_values(['logprob', 'science_freq'],  ascending=[True, False])
# df.to_csv('rare_in_askscience_comments.csv')
# print(df.head(n=50))

In [ ]:

science_comment_author_counts = Counter()

with open('all_comments_2018.jsonlist') as f:
    for line_i, line in enumerate(f):
        if line_i % 10000 == 0:
            print("{:d}".format(line_i), end="\r", flush=True)                    
        line = json.loads(line)
        if line['subreddit'] == 'EverythingScience':
            science_comment_author_counts.update(line['author'])        
print("")
print(len(science_comment_author_counts))


In [ ]:
# index = order[49178]
# print(common[index])
# print(science_comment_counts['being'])
# print(science_comments_N)
# print(bg_comment_counts['being'])
# print(bg_comments_N)
# print(science_comment_counts['being'] / science_comments_N)
# print(bg_comment_counts['being'] / bg_comments_N)
# print(stats.chisquare([science_comment_counts['being'],science_comments_N - science_comment_counts['being']],
#                      [bg_comment_counts['being'], bg_comments_N - bg_comment_counts['being']]))

# p = 1/0.00169
# print(p)
# print(2*592-2)
# print(stats.chisquare([1, 592-1], [2, 592*2-2]))

In [ ]:
# import numpy as np
# score_vals = [line['score'] for line in science]
# score_median = np.median(score_vals)
# print(np.median(score_vals))
# print(np.histogram(score_vals))
# comment_vals = [line['num_comments'] for line in science]
# comments_median = np.median(comment_vals)
# print(np.median(comment_vals))
# print(np.histogram(comment_vals))

In [ ]:
# score_vals = [line['score'] for line in science_comments]
# median_comment_score = np.median(score_vals)
# print(median_comment_score)


In [4]:
with open('data/cleaned/experienced_and_new_authors_comments.json', 'r') as f:
    users = json.load(f)
print(list(users.keys()))

['science', 'news', 'politics', 'pics', 'funny', 'AskReddit', 'AskHistorians', 'EverythingScience', 'Futurology', 'TrueReddit', 'dataisbeautiful', 'askscience']


In [5]:
science_users = users['EverythingScience']
print(list(science_users.keys()))

['experienced', 'new']


In [6]:
science_users_new = set(science_users['new'])
science_users_exp = set(science_users['experienced'])

In [8]:
science_comments_new_counts = Counter()
science_comments_exp_counts = Counter()
new_comments = 0
exp_comments = 0
with open('all_comments_2018.jsonlist') as f:
    for line_i, line in enumerate(f):
        if line_i % 10000 == 0:
            print("{:d}".format(line_i), end="\r", flush=True)                    
        line = json.loads(line)
        line = convert_to_tuple(line, ['body_tokens'])
        if line['subreddit'] == 'EverythingScience':
            if line['author'] in science_users_new: 
                science_comments_new_counts.update(line['body_tokens'])        
                new_comments +=1 
            elif line['author'] in science_users_exp: 
                science_comments_exp_counts.update(line['body_tokens'])        
                exp_comments += 1
print("")
print(len(science_comments_new_counts))
print(len(science_comments_exp_counts))

NameError: name 'convert_to_tuple' is not defined

In [ ]:
common = set()
common.update(science_comments_new_counts.keys())
common.update(science_comments_exp_counts.keys())
common = list(common)
common.sort()
print(len(common))
science_new_N = sum(science_comments_new_counts.values())
science_exp_N = sum(science_comments_exp_counts.values())
print(science_new_N, science_exp_N)

In [ ]:
smoothing = 0.1
vocab_size = len(common)
logprobs = []
pvals = []
for word in common:
    if word in science_comments_exp_counts:
        bg_c = science_comments_exp_counts[word] + smoothing
        bg_p = (science_comments_exp_counts[word] + smoothing) / float(science_exp_N + smoothing * len(common))
    else:
        bg_c = smoothing
        bg_p = (smoothing) / float(science_exp_N + smoothing * len(common))
    if word in science_comments_new_counts:
        count = science_comments_new_counts[word]
    else:
        count = 0
    logprob = stats.binom.logpmf(k=count, n=science_new_N, p=bg_p)
    logprobs.append(logprob)
    chisq, pval = stats.chisquare([count, science_new_N - count], 
                              [bg_c, science_exp_N + smoothing * vocab_size - bg_c])
    pvals.append(pval * vocab_size)

print(len(logprobs))

In [ ]:
order = np.argsort(logprobs)
df = pd.DataFrame(columns=['word', 'logprob', 'pval', 'science_freq', 'bg_freq'])
for i in range(30000):
    word = common[order[i]]
    if word in science_comments_new_counts:
        sc_count = science_comments_new_counts[word]
    else:
        sc_count = 0
    if word in science_comments_exp_counts:
        bg_count = science_comments_exp_counts[word]
    else:
        bg_count = 0
    if sc_count / science_new_N > bg_count / science_exp_N:
        df.loc[i] = [word, logprobs[order[i]], pvals[order[i]], sc_count / science_new_N, bg_count / science_exp_N]
df = df.sort_values(['logprob', 'science_freq'],  ascending=[True, False])        
df.to_csv('common_in_new_user_EverythingScience_comments.csv')
print(df.head(n=50))

In [ ]:
order = np.argsort(logprobs)
df = pd.DataFrame(columns=['word', 'logprob', 'pval', 'science_freq', 'bg_freq'])
for i in range(30000):
    word = common[order[i]]
    if word in science_comments_new_counts:
        sc_count = science_comments_new_counts[word]
    else:
        sc_count = 0
    if word in science_comments_exp_counts:
        bg_count = science_comments_exp_counts[word]
    else:
        bg_count = 0
    if sc_count / science_new_N < bg_count / science_exp_N:
        df.loc[i] = [word, logprobs[order[i]], pvals[order[i]], sc_count / science_new_N, bg_count / science_exp_N]
df = df.sort_values(['logprob', 'science_freq'],  ascending=[True, False])        
df.to_csv('rare_in_new_user_EverythingScience_comments.csv')
print(df.head(n=50))

In [ ]:
# count = 0
# subset = []
# with open('all_comments_2018.jsonlist') as f:
#     for line_i, line in enumerate(f):
#         if line_i % 10000 == 0:
#             print("{:d} {:d}".format(line_i, count), end="\r", flush=True)                    
#         line = json.loads(line)
#         if line['subreddit'] == 'science':
#             text = line['body'].lower()
#             if 'this subreddit' in text:
#                 subset.append(line)
#                 count += 1